# HW4

## PROBLEM 1 

## (a) 

In [1]:
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score, f1_score,confusion_matrix,roc_auc_score, recall_score, roc_curve, precision_score
from sklearn.preprocessing import LabelEncoder
import pandas as pd
import numpy as np
import math

In [2]:

dataset = pd.read_csv('spambase.data', header = None)
dataset.head()
X = dataset.iloc[:, :-1]
Y = dataset[57]


In [3]:
train_X, test_X, train_Y, test_Y = train_test_split(X,Y,test_size = 0.25, random_state = 11)

In [4]:
train_Y

2063    0
3083    0
4149    0
975     1
2182    0
       ..
332     1
1293    1
4023    0
3775    0
1945    0
Name: 57, Length: 3450, dtype: int64

In [5]:
for i in [10,50, 100]:
    classifier =AdaBoostClassifier(
            DecisionTreeClassifier(),
            n_estimators = i
    )
    classifier.fit(train_X, train_Y)
    predictions = classifier.predict(train_X)
    print("For", i, "base classifiers......")
    print("Train Accuracy", accuracy_score(train_Y, predictions))
    print("Train Error", 1- accuracy_score(train_Y, predictions))
    print("Train Precesion", precision_score(train_Y,predictions))
    print("Train Recall", recall_score(train_Y, predictions))
    classifier.fit(test_X, test_Y)
    predictions = classifier.predict(test_X)
    print("Test Accuracy", accuracy_score(test_Y, predictions))
    print("Test Error", 1- accuracy_score(test_Y, predictions))
    print("Test Precesion", precision_score(test_Y,predictions))
    print("Test Recall", recall_score(test_Y, predictions))

For 10 base classifiers......
Train Accuracy 0.9997101449275362
Train Error 0.00028985507246381825
Train Precesion 1.0
Train Recall 0.9992619926199262
Test Accuracy 1.0
Test Error 0.0
Test Precesion 1.0
Test Recall 1.0
For 50 base classifiers......
Train Accuracy 0.9997101449275362
Train Error 0.00028985507246381825
Train Precesion 1.0
Train Recall 0.9992619926199262
Test Accuracy 1.0
Test Error 0.0
Test Precesion 1.0
Test Recall 1.0
For 100 base classifiers......
Train Accuracy 0.9997101449275362
Train Error 0.00028985507246381825
Train Precesion 1.0
Train Recall 0.9992619926199262
Test Accuracy 1.0
Test Error 0.0
Test Precesion 1.0
Test Recall 1.0


## (b) 

In [6]:

for i in [10,50, 100]:
    model = RandomForestClassifier(
            n_estimators = i
    )
    model.fit(train_X, train_Y)
    predictions = model.predict(train_X)
    print("For", i, "decision trees......")
    print("Train Accuracy", accuracy_score(train_Y, predictions))
    print("Train Error", 1- accuracy_score(train_Y, predictions))
    print("Train Precesion", precision_score(train_Y,predictions))
    print("Train Recall", recall_score(train_Y, predictions))
    model.fit(test_X, test_Y)
    predictions = model.predict(test_X)
    print("Test Accuracy", accuracy_score(test_Y, predictions))
    print("Test Error", 1- accuracy_score(test_Y, predictions))
    print("Test Precesion", precision_score(test_Y,predictions))
    print("Test Recall", recall_score(test_Y, predictions))



For 10 decision trees......
Train Accuracy 0.9930434782608696
Train Error 0.006956521739130417
Train Precesion 0.9970126960418223
Train Recall 0.985239852398524
Test Accuracy 0.9930495221546481
Test Error 0.0069504778453518545
Test Precesion 0.9977876106194691
Test Recall 0.9847161572052402
For 50 decision trees......
Train Accuracy 0.9997101449275362
Train Error 0.00028985507246381825
Train Precesion 0.9992625368731564
Train Recall 1.0
Test Accuracy 1.0
Test Error 0.0
Test Precesion 1.0
Test Recall 1.0
For 100 decision trees......
Train Accuracy 0.9997101449275362
Train Error 0.00028985507246381825
Train Precesion 1.0
Train Recall 0.9992619926199262
Test Accuracy 1.0
Test Error 0.0
Test Precesion 1.0
Test Recall 1.0


## (c)

As number of base classifiers increases, accuracy increases. Comparing AdaBoost with RandomForest, AdBoost performs best with high accuracies than RandomForests

## PROBLEM 2

## (a) 

In [7]:
 model = DecisionTreeClassifier(
     #criterion = 'entropy',
            max_depth = 1
             
    )
model.fit(train_X, train_Y)
predictions = model.predict(train_X)

print("Train Accuracy", accuracy_score(train_Y, predictions))
print("Train Error", 1- accuracy_score(train_Y, predictions))
print("Train Precesion", precision_score(train_Y,predictions))
print("Train Recall", recall_score(train_Y, predictions))

Train Accuracy 0.7956521739130434
Train Error 0.20434782608695656
Train Precesion 0.7263231197771588
Train Recall 0.7697416974169742


## (b) 

In [23]:
def Ada_Boost(X, y, X_test,n_est):
    w =np.ones(len(y))/len(y)
    weight = []
    weight.append(w.copy())
    pred = []
    pred_test = []
    models = []
    beta_list = []
    error_list = []
    h = []
    for i in range(n_est):
        mod = DecisionTreeClassifier(max_depth = 1)
        mod.fit(X,y,np.array(w))
        models.append(mod)
        y_pred = mod.predict(X)
        mis = (y_pred!= y)
        error = np.dot(mis,w)
        error_list.append(error)
        beta = 0.5 * np.log((1-error)/error)
        beta_list.append(beta)
        w = w*np.exp(-beta * y_pred *y)
        w = w/np.sum(w)
        weight.append(w.copy())
    
    for k in range(len(models)):
        p = (models[k].predict(X))* beta_list[k]
        p_test = (models[k].predict(X_test))* beta_list[k]
        pred.append(p)
        pred_test.append(p_test)
    pred_a = np.array(pred)
    pred_a_test = np.array(pred_test)
    pred_train = np.sign(np.sum(pred_a, axis = 0))
    pred_test = np.sign(np.sum(pred_a_test, axis = 0))
    return pred_train, pred_test
    

## (c) 

In [25]:


for i in [1,50, 100, 150]:
    pred_train, pred_test = Ada_Boost(train_X, train_Y, test_X, i)
    print("For T=", i )
    print("Train Accuracy", accuracy_score(train_Y, pred_train))
    print("Train Error", 1- accuracy_score(train_Y, pred_train))
    print("Train Precesion", precision_score(train_Y,pred_train))
    print("Train Recall", recall_score(train_Y, pred_train))
    model.fit(test_X, test_Y)
    predictions = model.predict(test_X)
    print("Test Accuracy", accuracy_score(test_Y, pred_test))
    print("Test Error", 1- accuracy_score(test_Y, pred_test))
    print("Test Precesion", precision_score(test_Y,pred_test))
    print("Test Recall", recall_score(test_Y, pred_test))



For T= 1
Train Accuracy 0.7956521739130434
Train Error 0.20434782608695656
Train Precesion 0.7263231197771588
Train Recall 0.7697416974169742
Test Accuracy 0.7784535186794093
Test Error 0.22154648132059074
Test Precesion 0.7017892644135189
Test Recall 0.7707423580786026
For T= 50
Train Accuracy 0.8107246376811594
Train Error 0.18927536231884057
Train Precesion 0.6907608695652174
Train Recall 0.9380073800738007
Test Accuracy 0.789748045178106
Test Error 0.21025195482189396
Test Precesion 0.6646341463414634
Test Recall 0.9519650655021834
For T= 100
Train Accuracy 0.8107246376811594
Train Error 0.18927536231884057
Train Precesion 0.6907608695652174
Train Recall 0.9380073800738007
Test Accuracy 0.789748045178106
Test Error 0.21025195482189396
Test Precesion 0.6646341463414634
Test Recall 0.9519650655021834
For T= 150
Train Accuracy 0.8107246376811594
Train Error 0.18927536231884057
Train Precesion 0.6907608695652174
Train Recall 0.9380073800738007
Test Accuracy 0.789748045178106
Test Error

## (d)

In [38]:
class DecisionTree(object):
    def __init__(self, max_depth):
        self.depth = 0
        self.max_depth = max_depth
        self.column_name = []
    def entropy(self, division):
        print("entering entropy")
        s = 0
        n = len(division)
        classes = set(division)
        for c in classes:
            n_c = sum(division==c)
            if n_c == 0:
                e = 0
            else:
                e = -1*n_c*1.0/n* math.log(n_c*1.0/n,2)
            s += e
        return s, n
    def get_entropy(self, y_predict, y_real):
        print("entering get entropy")
        if len(y_predict) != len(y_real):
            return None
        n = len(y_real)
        print("entring first")
        s_true, n_true = self.entropy(y_real[y_predict])
        print("entring second")
        s_false, n_false = self.entropy(y_real[~y_predict])
        print("exiting")
        s = n_true*1.0/n *s_true + n_false* 1.0/n * s_false
        print(s)
        return s
    
    def find_best_split(self, col,y):
        print("entering find best split")
        min_entropy = 100
        n = len(y)
        for value in set(col):
            y_predict = col<value 
            my_entropy = self.get_entropy(y_predict, y)
                
            if my_entropy < min_entropy:
                min_entropy = my_entropy
                cutoff  = value
        return min_entropy, cutoff            
    def find_best_split_of_all(self, x,y):
        print("entering find bestsplit of all")
        col = None
        min_entropy = 100
        cutoff = None
        for i, c in enumerate(x.T):
            entropy, cur_cutoff = self.find_best_split(c,y)
            if entropy == 0:
                return i, curr_cutoff, entropy
            elif entropy < min_entropy:
                min_entropy = entropy
                col = i
                cutoff = cur_cutoff
        return col, cutoff, min_entropy
    def fit(self, x, y, col_name, depth = 0):
        print("entering fit")
        if col_name != []:
            self.column_name = col_name
        labels = set(y)
        if len(y) == 0:
            return None
        max_label_cnt = 0
        val = y[0]
        list_labels = []
        for label in labels:
            list_labels.append({label : (y==label).sum()})
            if (y==label).sum() > max_label_cnt:
                val = label
                max_label_cnt = (y==label).sum()
            if len(np.unique(y)) == 1:
                par_node = {'val' : y[0]}
                return par_node
            elif depth >= self.max_depth:
                par_node = {'val': val}
                return par_node
            else:
                col,cutoff,entropy = self.find_best_split_of_all(x,y)
                cur_entropy, cur_n = self.entropy(y)
                
                if cur_entropy <= entropy:
                    par_node = {'val': val}
                    return par_node
                
                y_left = y[x[:,col] < cutoff]
                y_right = y[x[:,col]>= cutoff]
                par_node = {
                    'col': self.column_name[col],
                    'index_col': col,
                    'cutoff': cutoff,
                    'val': val
                }
                
                par_node['left'] = self.fit(x[x[:,col] < cutoff], y_left, [], depth+1)
                par_node['righht'] = self.fit(x[x[:, col]>= cutoff], y_right, [], depth+1)
                
                delf.depth +=1
                self.trees = par_node
                return par_node
    def predict(self, x):
        results = np.array([0]*len(x))
        for i, c in enumerate(x):
            results[i] = self._get_prediction(c)
        return results
    def _get_prediction(self, row):
        cur_layer = self.trees
        while cur_layer.get('cutoff'):
            if row[cur_layer['index_col']] < cur_layer['cutoff']:
                cur_layer = cur_layer['left']
            else:
                cur_layer = cur_layer['right']
        else:
            return cur_layer.get('val')
            
            
            
            
                  

In [39]:
x = np.array(train_X)
y = np.array(train_Y)
c = list(train_X.columns)
clf = DecisionTree(max_depth = 3)
m = clf.fit(x,y,c)


entering fit
entering find bestsplit of all
entering find best split
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9665535865540422
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9665477272610385
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9645261518517659
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9664691374530906
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.958598264247608
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.965715525607373
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9659056705891264
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9663106055991177
entering get entropy
entring first
entering e

entring second
entering entropy
exiting
0.9657588509313665
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9607173115452263
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9663248997940114
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9650915108731678
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9448216042910609
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9628293904957886
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9660800942444024
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9218739158284224
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9178556338697156
entering get entropy
entring first
entering entropy
e

entring second
entering entropy
exiting
0.9660882599681253
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9636291550674706
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9523096758522932
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.966513392108161
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9651462016386525
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9622055407057732
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9660506719903922
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9600492306997993
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.962671508182255
entering get entropy
entring first
entering entropy
ent

entering entropy
entring second
entering entropy
exiting
0.9621066383520829
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9542724726839177
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9641728323133315
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9647104738805229
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9613478856758996
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9378006416361179
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9320391652324742
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9339515938535328
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9358336381456396
entering get entropy
entring first
e

entering entropy
entring second
entering entropy
exiting
0.9664958562019834
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9665428835505002
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9662582703914443
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9661505736484594
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9649272530524351
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9661797031824637
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9660367336730333
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.9092977638297255
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.8767679023950823
entering get entropy
entring first
e

...

entering entropy
entring second
entering entropy
exiting
0.47624284719141124
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4760638479995689
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47600315783155456
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47642510221184
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47721557720839347
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47758355514608114
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47753409877500347
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4774841521720263
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47738277613922087
entering get entropy
entring fir

entering entropy
entring second
entering entropy
exiting
0.4775215740198774
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47746035660914793
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4773983461723668
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4773355347223248
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4776915789407013
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4776314159064087
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4775704459126548
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4775086606197748
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.47791754398826836
entering get entropy
entring first

entering entropy
entring second
entering entropy
exiting
0.48065003013754526
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.48064071308313283
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.48063031202440476
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4806188036830601
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.48060616398099293
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.48059236800328187
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4805773899590119
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.480561203139771
entering get entropy
entring first
entering entropy
entring second
entering entropy
exiting
0.4805437798756566
entering get entropy
entring fir

entering fit
entering fit


NameError: name 'delf' is not defined

In [ ]:
m

## PROBLEM 3

## (b)

In [41]:
from numpy import loadtxt
from keras.models import Sequential
from keras.layers import Dense
import numpy
import tensorflow as tf
import idx2numpy

Using TensorFlow backend.


In [42]:
X_train = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/train-images.idx3-ubyte')
Y_train = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/train-labels.idx1-ubyte')
X_test = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/t10k-images.idx3-ubyte')
Y_test = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/t10k-labels.idx1-ubyte')
print(X_train.shape)
print(Y_train.shape)
X_train = X_train.reshape(60000, 784)
X_train = X_train.astype('float32')
X_test = X_test.reshape(10000, 784)
X_test = X_test.astype('float32')

X_train /= 255
X_test /= 255

(60000, 28, 28)
(60000,)


In [45]:
from keras.models import Sequential
from keras.layers import Dense, Conv2D, Dropout, Flatten, MaxPooling2D

model = Sequential()
model.add(Dense(512, input_dim = 784, activation = 'relu'))

model.add(Dense(512, activation = 'relu'))

model.add(Dense(10, activation = 'softmax'))

model.compile(optimizer = 'adam',
              loss = 'sparse_categorical_crossentropy',
             metrics = ['accuracy'])

model.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model.summary()

Epoch 1/5
60000/60000 [==============================] - 54s 905us/step - loss: 0.1880 - acc: 0.9423
Epoch 2/5
60000/60000 [==============================] - 47s 791us/step - loss: 0.0939 - acc: 0.9721
Epoch 3/5
60000/60000 [==============================] - 52s 869us/step - loss: 0.0700 - acc: 0.9797
Epoch 4/5
60000/60000 [==============================] - 57s 953us/step - loss: 0.0591 - acc: 0.9827
Epoch 5/5
60000/60000 [==============================] - 56s 938us/step - loss: 0.0516 - acc: 0.9855
Train loss: 0.02975950699267014
Train accuracy: 0.9914666666666667
Train error: 0.008533333333333282
Epoch 1/5
10000/10000 [==============================] - 8s 813us/step - loss: 0.0882 - acc: 0.9776
Epoch 2/5
10000/10000 [==============================] - 9s 877us/step - loss: 0.0330 - acc: 0.9896
Epoch 3/5
10000/10000 [==============================] - 9s 870us/step - loss: 0.0202 - acc: 0.9940
Epoch 4/5
10000/10000 [==============================] - 9s 904us/step - loss: 0.0183 - acc: 0

In [46]:
model1 = Sequential()

model1.add(Dense(210, input_dim = 784, activation = 'sigmoid'))

model1.add(Dense(210, activation = 'sigmoid'))
model1.add(Dense(150, activation = 'relu'))

model1.add(Dense(10,activation = 'softmax' ))

model1.compile(optimizer = 'adam',
              loss = 'sparse_categorical_crossentropy',
             metrics = ['accuracy'])

model1.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model1.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model1.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model1.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model1.summary()

Epoch 1/5
60000/60000 [==============================] - 41s 686us/step - loss: 0.2948 - acc: 0.9095
Epoch 2/5
60000/60000 [==============================] - 33s 558us/step - loss: 0.1188 - acc: 0.9636
Epoch 3/5
60000/60000 [==============================] - 33s 546us/step - loss: 0.0798 - acc: 0.9759
Epoch 4/5
60000/60000 [==============================] - 40s 667us/step - loss: 0.0588 - acc: 0.9816
Epoch 5/5
60000/60000 [==============================] - 30s 504us/step - loss: 0.0454 - acc: 0.9857
Train loss: 0.039738856237210955
Train accuracy: 0.9872166666666666
Train error: 0.012783333333333369
Epoch 1/5
10000/10000 [==============================] - 5s 518us/step - loss: 0.0767 - acc: 0.9772
Epoch 2/5
10000/10000 [==============================] - 5s 507us/step - loss: 0.0350 - acc: 0.9884
Epoch 3/5
10000/10000 [==============================] - 5s 517us/step - loss: 0.0174 - acc: 0.9941
Epoch 4/5
10000/10000 [==============================] - 5s 527us/step - loss: 0.0133 - acc: 

In [47]:
model2 = Sequential()

model2.add(Dense(10, input_dim = 784, activation = 'sigmoid'))

model2.add(Dense(10, activation = 'sigmoid'))
model2.add(Dense(10, activation = 'relu'))
model2.add(Dense(10, activation = 'relu'))

model2.add(Dense(10,activation = 'softmax' ))

model2.compile(optimizer = 'adam',
              loss = 'sparse_categorical_crossentropy',
             metrics = ['accuracy'])

model2.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model2.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model2.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model2.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model2.summary()

Epoch 1/5
60000/60000 [==============================] - 12s 199us/step - loss: 0.9470 - acc: 0.7153
Epoch 2/5
60000/60000 [==============================] - 11s 188us/step - loss: 0.5182 - acc: 0.8654
Epoch 3/5
60000/60000 [==============================] - 11s 190us/step - loss: 0.4031 - acc: 0.8937
Epoch 4/5
60000/60000 [==============================] - 11s 190us/step - loss: 0.3373 - acc: 0.9078
Epoch 5/5
60000/60000 [==============================] - 11s 188us/step - loss: 0.3047 - acc: 0.9156
Train loss: 0.28995516640643276
Train accuracy: 0.9185166666666666
Train error: 0.08148333333333335
Epoch 1/5
10000/10000 [==============================] - 2s 202us/step - loss: 0.3105 - acc: 0.9141
Epoch 2/5
10000/10000 [==============================] - 2s 194us/step - loss: 0.2772 - acc: 0.9225
Epoch 3/5
10000/10000 [==============================] - 2s 201us/step - loss: 0.2587 - acc: 0.9286
Epoch 4/5
10000/10000 [==============================] - 2s 224us/step - loss: 0.2404 - acc: 0.

## (c)

In [48]:
X_train = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/train-images.idx3-ubyte')
Y_train = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/train-labels.idx1-ubyte')
X_test = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/t10k-images.idx3-ubyte')
Y_test = idx2numpy.convert_from_file('C:/Users/Aishwarya/Desktop/NEU/SML/hw4/t10k-labels.idx1-ubyte')
print(X_train.shape)

X_train = X_train.reshape(X_train.shape[0], 28, 28, 1)
X_test = X_test.reshape(X_test.shape[0], 28, 28, 1)
input_shape = (28, 28, 1)

# Making sure that the values are float so that we can get decimal points after division
X_train = X_train.astype('float32')
X_test = X_test.astype('float32')
# Normalizing the RGB codes by dividing it to the max RGB value.
X_train /= 255
X_test /= 255



(60000, 28, 28)


In [49]:
# Creating a Sequential Model and adding the layers
model = Sequential()
model.add(Conv2D(28, kernel_size=(3,3), input_shape=input_shape))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Flatten()) # Flattening the 2D arrays for fully connected layers
model.add(Dense(128, activation=tf.nn.relu))
model.add(Dropout(0.2))
model.add(Dense(10,activation=tf.nn.softmax))
model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy', 
              metrics=['accuracy'])
model.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model.summary()



Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.
Epoch 1/5
60000/60000 [==============================] - 77s 1ms/step - loss: 0.1906 - acc: 0.9416
Epoch 2/5
60000/60000 [==============================] - 77s 1ms/step - loss: 0.0856 - acc: 0.9734
Epoch 3/5
60000/60000 [==============================] - 59069s 984ms/step - loss: 0.0605 - acc: 0.9810
Epoch 4/5
60000/60000 [==============================] - 84s 1ms/step - loss: 0.0497 - acc: 0.9848
Epoch 5/5
60000/60000 [==============================] - 81s 1ms/step - loss: 0.0417 - acc: 0.9869
Train loss: 0.016872691329549706
Train accuracy: 0.9946833333333334
Train error: 0.005316666666666636
Epoch 1/5
10000/10000 [==============================] - 15s 2ms/step - loss: 0.0797 - acc: 0.9775
Epoch 2/5
10000/10000 [==============================] - 13s 1ms/step - loss: 0.0335 - acc: 0.9895
Epoch 3/5
10000/10000 [==============================] - 12s 1ms/step - loss: 0.023

In [50]:
model = Sequential()
model.add(Conv2D(28, kernel_size=(4,4), input_shape=input_shape))
model.add(MaxPooling2D(pool_size=(3, 3)))
model.add(Flatten()) # Flattening the 2D arrays for fully connected layers
model.add(Dense(128, activation=tf.nn.relu))
model.add(Dense(128, activation=tf.nn.tanh))
model.add(Dropout(0.2))
model.add(Dense(10,activation=tf.nn.softmax))
model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy', 
              metrics=['accuracy'])
model.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model.summary()

Epoch 1/5
60000/60000 [==============================] - 73s 1ms/step - loss: 0.1303 - acc: 0.9602
Epoch 2/5
60000/60000 [==============================] - 68s 1ms/step - loss: 0.0535 - acc: 0.9840
Epoch 3/5
60000/60000 [==============================] - 65s 1ms/step - loss: 0.0366 - acc: 0.9891
Epoch 4/5
60000/60000 [==============================] - 60s 993us/step - loss: 0.0290 - acc: 0.9915
Epoch 5/5
60000/60000 [==============================] - 60s 996us/step - loss: 0.0240 - acc: 0.9926
Train loss: 0.013910045721313994
Train accuracy: 0.9956333333333334
Train error: 0.00436666666666663
Epoch 1/5
10000/10000 [==============================] - 10s 1ms/step - loss: 0.0524 - acc: 0.9852
Epoch 2/5
10000/10000 [==============================] - 10s 1ms/step - loss: 0.0167 - acc: 0.9941
Epoch 3/5
10000/10000 [==============================] - 10s 1ms/step - loss: 0.0085 - acc: 0.9974
Epoch 4/5
10000/10000 [==============================] - 10s 1ms/step - loss: 0.0029 - acc: 0.9993
Epoc

In [51]:
model = Sequential()

model.add(Conv2D(10, kernel_size=(3,3), input_shape=input_shape))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Conv2D(5, kernel_size=(3,3),activation = 'tanh' ))
model.add(MaxPooling2D(pool_size=(2, 2)))
model.add(Flatten()) # Flattening the 2D arrays for fully connected layers
model.add(Dense(64, activation=tf.nn.relu))
model.add(Dropout(0.2))
model.add(Dense(10,activation=tf.nn.softmax))
model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy', 
              metrics=['accuracy'])
model.fit(X_train, Y_train, epochs = 5, batch_size = 10)
score = model.evaluate(X_train, Y_train, verbose=0)
print('Train loss:', score[0])
print('Train accuracy:', score[1])
print('Train error:', 1- score[1])

model.fit(X_test, Y_test, epochs = 5, batch_size = 10)
score = model.evaluate(X_test, Y_test, verbose=0)
print('Test loss:', score[0])
print('Test accuracy:', score[1])
print('Train error:', 1- score[1])
model.summary()

Epoch 1/5
60000/60000 [==============================] - 40s 673us/step - loss: 0.2425 - acc: 0.9270
Epoch 2/5
60000/60000 [==============================] - 39s 657us/step - loss: 0.1061 - acc: 0.9668
Epoch 3/5
60000/60000 [==============================] - 39s 643us/step - loss: 0.0833 - acc: 0.9743
Epoch 4/5
60000/60000 [==============================] - 40s 660us/step - loss: 0.0730 - acc: 0.9772
Epoch 5/5
60000/60000 [==============================] - 41s 679us/step - loss: 0.0668 - acc: 0.9797
Train loss: 0.03429661646850097
Train accuracy: 0.9894833333333334
Train error: 0.010516666666666619
Epoch 1/5
10000/10000 [==============================] - 8s 801us/step - loss: 0.0638 - acc: 0.9805
Epoch 2/5
10000/10000 [==============================] - 8s 805us/step - loss: 0.0527 - acc: 0.9834
Epoch 3/5
10000/10000 [==============================] - 8s 798us/step - loss: 0.0409 - acc: 0.9863
Epoch 4/5
10000/10000 [==============================] - 8s 837us/step - loss: 0.0392 - acc: 0